In [1]:
from typing import List, Optional, Any
import torch
import torch.utils.data
import numpy as np
import random

import datetime

import transformers
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

from peft import LoraConfig
from trl import SFTTrainer
import datasets
import time

import json
import os
import cqlcmp

In [2]:
torch.manual_seed(21)
torch.cuda.manual_seed_all(21)
np.random.seed(21)
random.seed(21)
#torch.backends.cudnn.deterministic = True
#torch.backends.cudnn.benchmark = False

In [3]:
device = torch.device("cuda")

In [4]:
class DatasetNatural2CQL(torch.utils.data.Dataset):
    def __init__(self, path: Optional[str] = None) -> None:
        self.sentence_freq = []
        self.cql2nl = []
        self.nl2cql = []
        self.natural_language_rulebased = []
        self.cql = []
        self.natural_language = []
        self.enabled_natural_language = []

        if path is not None:
            self.load_tsv(path)

    def enable_cql(self, cqls):
        self.enabled_natural_language = []
        for cql in cqls:
            for p in cql:
                self.enabled_natural_language.append(p)

    def dump_json(self, filepath: str) -> None:
        with open(filepath, "w") as file:
            for i in range(len(self)):
                data = json.dumps(self[i])
                file.write(data)
                file.write("\n")

    def add_translation(self, freq: int, cql: str, natural_language_rulebased: str, natural_language: List[str]) -> None:
        cql_index = len(self.sentence_freq)
        self.sentence_freq.append(freq)
        self.cql.append(cql)
        self.natural_language_rulebased.append(natural_language_rulebased)
        self.cql2nl.append([])

        for sentence in natural_language:
            self.nl2cql.append(cql_index)
            self.cql2nl[-1].append(len(self.natural_language))
            self.natural_language.append(sentence)

    def load_tsv(self, path: str) -> None:
        with open(path, "r") as file_data:
            for line in file_data:
                line = line.strip()
                line = line.split("\t")
                texts_json = json.loads(line[4])
                texts_extracted = texts_json["data"][0]["content"][0]["text"]["value"].split("\n")
                self.add_translation(int(line[0]), line[2], line[3], texts_extracted)

    def __len__(self):
        return len(self.enabled_natural_language)

    def __getitem__(self, idx):
        if idx < len(self.nl2cql):
            return {"text": self.natural_language[self.enabled_natural_language[idx]], "cql": self.cql[self.nl2cql[self.enabled_natural_language[idx]]]}
        return None

In [5]:
dataset = DatasetNatural2CQL("expand_natural_texts_0004.res.tsv")

In [6]:
validation_cqls = []
with open("validation_ids.json", "r") as file:
    validation_cqls = json.load(file)

In [7]:
dataset.enable_cql(validation_cqls)

In [8]:
len(dataset)

16840

In [9]:
model_name = "meta-llama/Llama-3.2-1B"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name, quantization_config=bnb_config, device_map={"":0})

In [10]:
from peft import PeftConfig, PeftModel
from transformers import AutoModelForCausalLM, AutoTokenizer

base_model_name = "meta-llama/Llama-3.2-1B"
adapter_model_name = "outputs/checkpoint-102000"

model_orig = AutoModelForCausalLM.from_pretrained(model_name, quantization_config=bnb_config, device_map={"":0})
model = PeftModel.from_pretrained(model_orig, adapter_model_name)
model = model.to(device)

tokenizer = AutoTokenizer.from_pretrained(base_model_name)

In [11]:
import os

path = 'outputs'

# List all folders (directories) in the given path
folders = [name for name in os.listdir(path) if os.path.isdir(os.path.join(path, name))]

In [12]:
def f_in(data):
    full_input = """Translate Natural Language into CQL Queries like:

Word dog followed by lemma run, and then followed by a noun. CQL:
```
[word="dog"][lemma="run"][pos="NN"]
```

Lemma "be" optionally followed by the word "not". CQL:
```
[lemma="be"][word="not"]? 
```

""" + data + " CQL:\n```\n"
    return full_input

In [13]:
random.shuffle(dataset.enabled_natural_language)

i = 0
while i < len(dataset):
    dataset.natural_language[dataset.enabled_natural_language[i]] = f_in(dataset.natural_language[dataset.enabled_natural_language[i]])
    i += 1

In [14]:
tokenizer.pad_token = tokenizer.eos_token

In [15]:
def get_cql(text):
    text = text.split("<eos>")[0]
    text = text.split("CQL:")[3]
    text = text.split("```")[1]
    return text.strip()

In [ ]:
with open("validation_log.txt", "w") as log:
    for folder in folders:
        start_time = int(time.time())
        adapter_model_name = "outputs/" + folder

        if folder not in ["checkpoint-10500", "checkpoint-21000", "checkpoint-32000", "checkpoint-42500", "checkpoint-53000", "checkpoint-63500", "checkpoint-74500", "checkpoint-85000", "checkpoint-95500", "checkpoint-106230"]:
            continue
        
        model = PeftModel.from_pretrained(model_orig, adapter_model_name)
        dataloader = torch.utils.data.DataLoader(dataset, batch_size=256, shuffle=False)
        blue_sum = 0
        blue_size = 0
        batch_id = 0
        for batch in dataloader:
            batch_id += 1
            inputs = tokenizer(batch["text"], truncation=True, max_length=1024, return_tensors="pt", padding=True).to(device)
            outputs = model.generate(**inputs, max_new_tokens=100)
            for i, output in enumerate(outputs):
                cql = get_cql(tokenizer.decode(output, skip_special_tokens=True))
                cql_ids = cqlcmp.cql_tokenizer(cql)
                gold_cql_ids = cqlcmp.cql_tokenizer(batch["cql"][i])
                bleu = cqlcmp.sentence_bleu([gold_cql_ids], cql_ids, weights=(0.25, 0.25, 0.25, 0.25))
                blue_sum += bleu
                blue_size += 1
            to_log = ""
            to_log += "Working on: " + adapter_model_name + " | "
            to_log += str(blue_size) + "/" + str(len(dataset)) + " | "
            to_log += "AVG Bleu: " + str(blue_sum/blue_size) + " | "
            to_log += "Time: " + str(int(time.time())-start_time) + " | "
            to_log += "ETA: " + str(int((int(time.time())-start_time)/(blue_size/len(dataset)*(1-(blue_size/len(dataset)))))) + " sec" + " | "
            
            print(to_log, file=log)
            log.flush()
            print(to_log)
            if batch_id >= 15:
                break
            

/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/peft/tuners/tuners_utils.py:167: UserWarning: Already found a `peft_config` attribute in the model. This will lead to having multiple adapters in the model. Make sure to know what you are doing!
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aipr

Working on: outputs/checkpoint-85000 | 256/16840 | AVG Bleu: 0.34056641249951397 | Time: 68 | ETA: 4542 sec | 


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


Working on: outputs/checkpoint-85000 | 512/16840 | AVG Bleu: 0.3647611378475755 | Time: 187 | ETA: 6343 sec | 


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


...

Working on: outputs/checkpoint-32000 | 3584/16840 | AVG Bleu: 0.3626121598995242 | Time: 4695 | ETA: 28024 sec | 


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


Working on: outputs/checkpoint-32000 | 3840/16840 | AVG Bleu: 0.35911936512647225 | Time: 5035 | ETA: 28602 sec | 


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


Working on: outputs/checkpoint-74500 | 256/16840 | AVG Bleu: 0.2572568549774034 | Time: 317 | ETA: 21174 sec | 
